# What is the notebook about?

## Problem - Taxi Environment Algorithms
This problem deals with a taxi environment and stochastic actions. The tasks you have to do are:
- Implement Policy Iteration
- Implement Modified Policy Iteration
- Implement Value Iteration
- Implement Gauss Seidel Value Iteration
- Visualize the results
- Explain the results

## How to use this notebook? 📝

- This is a shared template and any edits you make here will not be saved.**You
should make a copy in your own drive**. Click the "File" menu (top-left), then "Save a Copy in Drive". You will be working in your copy however you like.

- **Update the config parameters**. You can define the common variables here

Variable | Description
--- | ---
`AICROWD_DATASET_PATH` | Path to the file containing test data. This should be an absolute path.
`AICROWD_RESULTS_DIR` | Path to write the output to.
`AICROWD_ASSETS_DIR` | In case your notebook needs additional files (like model weights, etc.,), you can add them to a directory and specify the path to the directory here (please specify relative path). The contents of this directory will be sent to AIcrowd for evaluation.
`AICROWD_API_KEY` | In order to submit your code to AIcrowd, you need to provide your account's API key. This key is available at https://www.aicrowd.com/participants/me

- **Installing packages**. Please use the [Install packages 🗃](#install-packages-) section to install the packages

# Setup AIcrowd Utilities 🛠

We use this to bundle the files for submission and create a submission on AIcrowd. Do not edit this block.

In [2]:
!pip install aicrowd-cli > /dev/null 

# AIcrowd Runtime Configuration 🧷

Get login API key from https://www.aicrowd.com/participants/me

In [3]:
import os
import sys
AICROWD_DATASET_PATH = os.getenv("DATASET_PATH", os.getcwd()+"/13d77bb0-b325-4e95-a03b-833eb6694acd_a2_taxi_inputs.zip")
AICROWD_RESULTS_DIR = os.getenv("OUTPUTS_DIR", "results")


API Key valid
Saved API Key successfully!
13d77bb0-b325-4e95-a03b-833eb6694acd_a2_taxi_inputs.zip: 100% 31.2k/31.2k [00:00<00:00, 125kB/s]


In [5]:
!unzip $AICROWD_DATASET_PATH

Archive:  /content/13d77bb0-b325-4e95-a03b-833eb6694acd_a2_taxi_inputs.zip
   creating: inputs/
  inflating: inputs/inputs_base.npy  
  inflating: inputs/inputs_1.npy     
  inflating: inputs/inputs_0.npy     
  inflating: inputs/inputs_2.npy     
   creating: targets/
  inflating: targets/targets_2.npy   
  inflating: targets/targets_0.npy   
  inflating: targets/targets_1.npy   
  inflating: targets/targets_base.npy  


In [6]:
DATASET_DIR = 'inputs/'

## Taxi Environment

Read the environment to understand the functions, but do not edit anything

In [8]:
import numpy as np

class TaxiEnv_HW2:
    def __init__(self, states, actions, probabilities, rewards, initial_policy):
        self.possible_states = states
        self._possible_actions = {st: ac for st, ac in zip(states, actions)}
        self._ride_probabilities = {st: pr for st, pr in zip(states, probabilities)}
        self._ride_rewards = {st: rw for st, rw in zip(states, rewards)}
        self.initial_policy = initial_policy
        self._verify()

    def _check_state(self, state):
        assert state in self.possible_states, "State %s is not a valid state" % state

    def _verify(self):
        """ 
        Verify that data conditions are met:
        Number of actions matches shape of next state and actions
        Every probability distribution adds up to 1 
        """
        ns = len(self.possible_states)
        for state in self.possible_states:
            ac = self._possible_actions[state]
            na = len(ac)

            rp = self._ride_probabilities[state]
            assert np.all(rp.shape == (na, ns)), "Probabilities shape mismatch"
        
            rr = self._ride_rewards[state]
            assert np.all(rr.shape == (na, ns)), "Rewards shape mismatch"

            assert np.allclose(rp.sum(axis=1), 1), "Probabilities don't add up to 1"

    def possible_actions(self, state):
        """ Return all possible actions from a given state """
        self._check_state(state)
        return self._possible_actions[state]

    def ride_probabilities(self, state, action):
        """ 
        Returns all possible ride probabilities from a state for a given action
        For every action a list with the returned with values in the same order as self.possible_states
        """
        actions = self.possible_actions(state)
        ac_idx = actions.index(action)
        return self._ride_probabilities[state][ac_idx]

    def ride_rewards(self, state, action):
        actions = self.possible_actions(state)
        ac_idx = actions.index(action)
        return self._ride_rewards[state][ac_idx]

## Example of Environment usage

In [9]:
def check_taxienv():
    # These are the values as used in the pdf, but they may be changed during submission, so do not hardcode anything

    states = ['A', 'B', 'C']

    actions = [['1','2','3'], ['1','2'], ['1','2','3']]

    probs = [np.array([[1/2,  1/4,  1/4],
                    [1/16, 3/4,  3/16],
                    [1/4,  1/8,  5/8]]),

            np.array([[1/2,   0,     1/2],
                    [1/16,  7/8,  1/16]]),

            np.array([[1/4,  1/4,  1/2],
                    [1/8,  3/4,  1/8],
                    [3/4,  1/16, 3/16]]),]

    rewards = [np.array([[10,  4,  8],
                        [ 8,  2,  4],
                        [ 4,  6,  4]]),

            np.array([[14,  0, 18],
                        [ 8, 16,  8]]),

            np.array([[10,  2,  8],
                        [6,   4,  2],
                        [4,   0,  8]]),]
    initial_policy = {'A': '1', 'B': '1', 'C': '1'}

    env = TaxiEnv_HW2(states, actions, probs, rewards, initial_policy)
    print("All possible states", env.possible_states)
    print("All possible actions from state B", env.possible_actions('B'))
    print("Ride probabilities from state A with action 2", env.ride_probabilities('A', '2'))
    print("Ride rewards from state C with action 3", env.ride_rewards('C', '3'))

    base_kwargs = {"states": states, "actions": actions, 
                "probabilities": probs, "rewards": rewards,
                "initial_policy": initial_policy}
    return base_kwargs

base_kwargs = check_taxienv()
env = TaxiEnv_HW2(**base_kwargs)

All possible states ['A', 'B', 'C']
All possible actions from state B ['1', '2']
Ride probabilities from state A with action 2 [0.0625 0.75   0.1875]
Ride rewards from state C with action 3 [4 0 8]


## Task 1 - Policy Iteration
Run policy iteration on the environment and generate the policy and expected reward

In [32]:
# 1.1 Policy Iteration
def policy_iteration(taxienv, gamma):
    # A list of all the states
    states = taxienv.possible_states
    # Initial values
    values = {s: 0 for s in states}

    # This is a dictionary of states to policies -> e.g {'A': '1', 'B': '2', 'C': '1'}
    policy = taxienv.initial_policy.copy()

    ## Begin code here

    # Hints - 
    # Do not hardcode anything
    # Only the final result is required for the results
    # Put any extra data in "extra_info" dictonary for any plots etc
    # Use the helper functions taxienv.ride_rewards, taxienv.ride_probabilities,  taxienv.possible_actions
    # For terminating condition use the condition exactly mentioned in the pdf
    while True:
        while True:
            delta = 0
            prev_values = values.copy()
            for s in states:
                prob = taxienv.ride_probabilities(s,policy[s])
                rewards = taxienv.ride_rewards(s,policy[s])
                exp_reward = 0
                for p,r,s_dash in zip(prob,rewards,states):
                    exp_reward += p*(r + gamma*prev_values[s_dash])
                values[s] = exp_reward
                delta = max(delta,abs(values[s]-prev_values[s]))
            if delta < 1e-8:
                break

        done = 1
        prev_policy = policy.copy()
        for s in states:
            poss_actions = taxienv.possible_actions(s)
            best_action = ''
            max_exp_reward = -sys.maxsize - 1
            for a in poss_actions:
                prob = taxienv.ride_probabilities(s,a)
                rewards = taxienv.ride_rewards(s,a)
                exp_reward = 0
                for p,r,s_dash in zip(prob,rewards,states):
                    exp_reward += p*(r + gamma*values[s_dash])
                if exp_reward > max_exp_reward:
                    best_action = a
                    max_exp_reward = exp_reward
            policy[s] = best_action
            if policy[s] != prev_policy[s]:
                done = 0
    
        if done:
            break     

    # Put your extra information needed for plots etc in this dictionary
    extra_info = {}

    ## Do not edit below this line

    # Final results
    return {"Expected Reward": values, "Policy": policy}, extra_info

# Task 2 - Policy Iteration for multiple values of gamma

Ideally this code should run as is

In [33]:
# 1.2 Policy Iteration with different values of gamma
def run_policy_iteration(env):
    gamma_values = np.arange(5, 100, 5)/100
    results, extra_info = {}, {}
    for gamma in gamma_values:
        results[gamma], extra_info[gamma] = policy_iteration(env, gamma)
    return results, extra_info

results_pi, extra_info_pi = run_policy_iteration(env)

# Task 3 - Modifed Policy Iteration

Implement modified policy iteration (where Value iteration is done for fixed m number of steps)

In [50]:
# 1.3 Modified Policy Iteration
def modified_policy_iteration(taxienv, gamma, m):
    # A list of all the states
    states = taxienv.possible_states
    # Initial values
    values = {s: 0 for s in states}

    # This is a dictionary of states to policies -> e.g {'A': '1', 'B': '2', 'C': '1'}
    policy = taxienv.initial_policy.copy()

    ## Begin code here

    # Hints - 
    # Do not hardcode anything
    # Only the final result is required for the results
    # Put any extra data in "extra_info" dictonary for any plots etc
    # Use the helper functions taxienv.ride_rewards, taxienv.ride_probabilities,  taxienv.possible_actions
    # For terminating condition use the condition exactly mentioned in the pdf
    iterations = 0
    while True:
        iterations += 1
        for i in range(m):
            prev_values = values.copy()
            for s in states:
                prob = taxienv.ride_probabilities(s,policy[s])
                rewards = taxienv.ride_rewards(s,policy[s])
                exp_reward = 0
                for p,r,s_dash in zip(prob,rewards,states):
                    exp_reward += p*(r + gamma*prev_values[s_dash])
                values[s] = exp_reward
        done = 1
        prev_policy = policy.copy()
        for s in states:
            poss_actions = taxienv.possible_actions(s)
            best_action = ''
            max_exp_reward = -sys.maxsize - 1
            for a in poss_actions:
                prob = taxienv.ride_probabilities(s,a)
                rewards = taxienv.ride_rewards(s,a)
                exp_reward = 0
                for p,r,s_dash in zip(prob,rewards,states):
                    exp_reward += p*(r + gamma*values[s_dash])
                if exp_reward > max_exp_reward:
                    best_action = a
                    max_exp_reward = exp_reward
            policy[s] = best_action
            if policy[s] != prev_policy[s]:
                done = 0

        if done:
            break 
    
    # Put your extra information needed for plots etc in this dictionary
    extra_info = {"iterations": iterations}

    ## Do not edit below this line


    # Final results
    return {"Expected Reward": values, "Policy": policy}, extra_info

# Task 4 Modified policy iteration for multiple values of m

Ideally this code should run as is

In [51]:
def run_modified_policy_iteration(env):
    m_values = np.arange(1, 15)
    gamma = 0.9
    results, extra_info = {}, {}
    for m in m_values:
        results[m], extra_info[m] = modified_policy_iteration(env, gamma, m)
    return results, extra_info

results_mpi, extra_info_mpi = run_modified_policy_iteration(env)

# Task 5 Value Iteration

Implement value iteration and find the policy and expected rewards

In [85]:
# 1.4 Value Iteration
def value_iteration(taxienv, gamma):
    # A list of all the states
    states = taxienv.possible_states
    # Initial values
    values = {s: 0 for s in states}

    # This is a dictionary of states to policies -> e.g {'A': '1', 'B': '2', 'C': '1'}
    policy = taxienv.initial_policy.copy()

    ## Begin code here

    # Hints - 
    # Do not hardcode anything
    # Only the final result is required for the results
    # Put any extra data in "extra_info" dictonary for any plots etc
    # Use the helper functions taxienv.ride_rewards, taxienv.ride_probabilities,  taxienv.possible_actions
    # For terminating condition use the condition exactly mentioned in the pdf
    iterations = 0
    while True:
        iterations += 1
        delta = 0
        prev_policy = policy.copy()
        prev_values = values.copy()
        for s in states:
            poss_actions = taxienv.possible_actions(s)
            best_action = ''
            max_exp_reward = -sys.maxsize - 1
            for a in poss_actions:
                prob = taxienv.ride_probabilities(s,a)
                rewards = taxienv.ride_rewards(s,a)
                exp_reward = 0
                for p,r,s_dash in zip(prob,rewards,states):
                    exp_reward += p*(r + gamma*prev_values[s_dash])
                if exp_reward > max_exp_reward:
                    best_action = a
                    max_exp_reward = exp_reward
            values[s] = max_exp_reward
            delta = max(delta,abs(values[s]-prev_values[s]))
            policy[s] = best_action

        if delta < 1e-8:
            break   

    # Put your extra information needed for plots etc in this dictionary
    extra_info = {"iterations": iterations}

    ## Do not edit below this line

    # Final results
    return {"Expected Reward": values, "Policy": policy}, extra_info

# Task 6 Value Iteration with multiple values of gamma

Ideally this code should run as is

In [86]:
def run_value_iteration(env):
    gamma_values = np.arange(5, 100, 5)/100
    results = {}
    results, extra_info = {}, {}
    for gamma in gamma_values:
        results[gamma], extra_info[gamma] = value_iteration(env, gamma)
    return results, extra_info
  
results_vi, extra_info_vi = run_value_iteration(env)

# Task 7 Gauss Seidel Value Iteration

Implement Gauss Seidel Value Iteration

In [84]:
# 1.4 Gauss Seidel Value Iteration
def gauss_seidel_value_iteration(taxienv, gamma):
    # A list of all the states
    # For Gauss Seidel Value Iteration - iterate through the values in the same order
    states = taxienv.possible_states

    # Initial values
    values = {s: 0 for s in states}

    # This is a dictionary of states to policies -> e.g {'A': '1', 'B': '2', 'C': '1'}
    policy = taxienv.initial_policy.copy()

    # Hints - 
    # Do not hardcode anything
    # For Gauss Seidel Value Iteration - iterate through the values in the same order as taxienv.possible_states
    # Only the final result is required for the results
    # Put any extra data in "extra_info" dictonary for any plots etc
    # Use the helper functions taxienv.ride_rewards, taxienv.ride_probabilities,  taxienv.possible_actions
    # For terminating condition use the condition exactly mentioned in the pdf

    ## Begin code here
    iterations = 0
    while True:
        iterations += 1
        delta = 0
        prev_policy = policy.copy()
        prev_values = values.copy()
        for s in states:
            poss_actions = taxienv.possible_actions(s)
            best_action = ''
            max_exp_reward = -sys.maxsize - 1
            for a in poss_actions:
                prob = taxienv.ride_probabilities(s,a)
                rewards = taxienv.ride_rewards(s,a)
                exp_reward = 0
                for p,r,s_dash in zip(prob,rewards,states):
                    exp_reward += p*(r + gamma*values[s_dash])
                if exp_reward > max_exp_reward:
                    best_action = a
                    max_exp_reward = exp_reward
            values[s] = max_exp_reward
            delta = max(delta,abs(values[s]-prev_values[s]))
            policy[s] = best_action
            
        if delta < 1e-8:
            break 
    
    # Put your extra information needed for plots etc in this dictionary
    extra_info = {"iterations": iterations}

    ## Do not edit below this line

    # Final results
    return {"Expected Reward": values, "Policy": policy}, extra_info

# Task 8 Gauss Seidel Value Iteration with multiple values of gamma

Ideally this code should run as is

In [87]:
def run_gauss_seidel_value_iteration(env):
    gamma_values = np.arange(5, 100, 5)/100
    results = {}
    results, extra_info = {}, {}
    for gamma in gamma_values:
        results[gamma], extra_info[gamma] = gauss_seidel_value_iteration(env, gamma)
    return results, extra_info

results_gs, extra_info_gs = run_gauss_seidel_value_iteration(env)

# Generate Results ✅

In [88]:
# Do not edit this cell
def get_results(kwargs):

    taxienv = TaxiEnv_HW2(**kwargs)

    policy_iteration_results = run_policy_iteration(taxienv)[0]
    modified_policy_iteration_results = run_modified_policy_iteration(taxienv)[0]
    value_iteration_results = run_value_iteration(taxienv)[0]
    gs_vi_results = run_gauss_seidel_value_iteration(taxienv)[0]

    final_results = {}
    final_results["policy_iteration"] = policy_iteration_results
    final_results["modifed_policy_iteration"] = modified_policy_iteration_results
    final_results["value_iteration"] = value_iteration_results
    final_results["gauss_seidel_iteration"] = gs_vi_results

    return final_results

In [89]:
# Do not edit this cell, generate results with it as is
if not os.path.exists(AICROWD_RESULTS_DIR):
    os.mkdir(AICROWD_RESULTS_DIR)

for params_file in os.listdir(DATASET_DIR):
  kwargs = np.load(os.path.join(DATASET_DIR, params_file), allow_pickle=True).item()
  results = get_results(kwargs)
  idx = params_file.split('_')[-1][:-4]
  np.save(os.path.join(AICROWD_RESULTS_DIR, 'results_' + idx), results)

# Check your local score

This score is not your final score, and it doesn't use the marks weightages. This is only for your reference of how arrays are matched and with what tolerance.

In [99]:
# Check your score on the given test cases (There are more private test cases not provided)
target_folder = 'targets'
result_folder = AICROWD_RESULTS_DIR

def check_algo_match(results, targets):
    param_matches = []
    for k in results:
        param_results = results[k]
        param_targets = targets[k]
        policy_match = param_results['Policy'] == param_targets['Policy']
        rv = [v for k, v in param_results['Expected Reward'].items()]
        tv = [v for k, v in param_targets['Expected Reward'].items()]
        rewards_match = np.allclose(rv, tv, rtol=3)
        equal = rewards_match and policy_match
        param_matches.append(equal)
    return np.mean(param_matches)

def check_score(target_folder, result_folder):
    match = []
    for out_file in os.listdir(result_folder):
        res_file = os.path.join(result_folder, out_file)
        results = np.load(res_file, allow_pickle=True).item()
        idx = out_file.split('_')[-1][:-4]  # Extract the file number
        target_file = os.path.join(target_folder, f"targets_{idx}.npy")
        targets = np.load(target_file, allow_pickle=True).item()
        algo_match = []
        for k in targets:
            algo_results = results[k]
            algo_targets = targets[k]
            algo_match.append(check_algo_match(algo_results, algo_targets))
        match.append(np.mean(algo_match))
    return np.mean(match)

if os.path.exists(target_folder):
    print("Shared data Score (normalized to 1):", check_score(target_folder, result_folder))

Shared data Score (normalized to 1): 1.0


## Visualize results of Policy Iteration with multiple values of gamma

Add code to visualize the results

In [91]:
## Visualize policy iteration with multiple values of gamma
gamma_values = np.arange(5, 100, 5)/100
for gamma in gamma_values:
    print("FOR GAMMA ",gamma)
    print("the optimal reward")
    print(results_pi[gamma]["Expected Reward"])
    print("the optimal policy")
    print(results_pi[gamma]["Policy"])
    print()
    print("-------------------------------")

FOR GAMMA  0.05
the optimal reward
{'A': 8.511527294182539, 'B': 16.400259908653545, 'C': 7.498869066334438}
the optimal policy
{'A': '1', 'B': '1', 'C': '1'}

-------------------------------
FOR GAMMA  0.1
the optimal reward
{'A': 9.076506148654659, 'B': 16.856368562663413, 'C': 8.050865123013633}
the optimal policy
{'A': '1', 'B': '1', 'C': '1'}

-------------------------------
FOR GAMMA  0.15
the optimal reward
{'A': 9.708121492773689, 'B': 17.46450304225433, 'C': 8.66916045381265}
the optimal policy
{'A': '1', 'B': '2', 'C': '1'}

-------------------------------
FOR GAMMA  0.2
the optimal reward
{'A': 10.437030073770368, 'B': 18.482142855718322, 'C': 9.384398494823}
the optimal policy
{'A': '1', 'B': '2', 'C': '1'}

-------------------------------
FOR GAMMA  0.25
the optimal reward
{'A': 11.274074071593612, 'B': 19.62962962714457, 'C': 10.207407404926943}
the optimal policy
{'A': '1', 'B': '2', 'C': '1'}

-------------------------------
FOR GAMMA  0.3
the optimal reward
{'A': 12.24

# Subjective questions


## 1.a How are values of $\gamma$ affecting results of policy iteration

From the results of policy iteraion for different values of gamma we can see that as the values of gamma increases the optimal reward also increases.This is bacause with increasing gamma the algorithm looks more and more into the distant future.For small values of gamma the algorithm looks into only immediate reward and thus chooses action based on it.And so initially the optimal action is to take action 1 i.e cruise the streets looking for a passenger. But if we look into further future then the optimal action is 2 i.e go to the nearest taxi stand and wait in line. 

## 1.b For modified policy itetaration, do you find any improvement if you choose m=10.

Yes,if we choose m  = 10 then there is improvement over m = 5,as the optimal reward increases and becomes closer to the value obtained by policy iteration for gamma = 0.9.This is because in m = 10,better approximate value of J is obtained as bellman operator for a particular policy is applied more times i.e 10 and then policy updation is done rather than bellman operator applied for less times i.e 5 and then updation of policy.

In [92]:
m_values = np.arange(1, 11)
for m in m_values:
    print("FOR m ",m)
    print("the optimal reward for gamma 0.9")
    print(results_mpi[m]["Expected Reward"])
    print("the optimal policy")
    print(results_mpi[m]["Policy"])
    print("the number of iterations required to converge",extra_info_mpi[m]["iterations"])
    print("------------------------------------")



FOR m  1
the optimal reward for gamma 0.9
{'A': 25.675390625, 'B': 39.27046874999999, 'C': 26.9415625}
the optimal policy
{'A': '2', 'B': '2', 'C': '2'}
the number of iterations required to converge 3
------------------------------------
FOR m  2
the optimal reward for gamma 0.9
{'A': 48.55490468521119, 'B': 62.203121287078865, 'C': 49.737400154724135}
the optimal policy
{'A': '2', 'B': '2', 'C': '2'}
the number of iterations required to converge 3
------------------------------------
FOR m  3
the optimal reward for gamma 0.9
{'A': 66.5070336319201, 'B': 80.16002669080505, 'C': 67.69034691854696}
the optimal policy
{'A': '2', 'B': '2', 'C': '2'}
the number of iterations required to converge 3
------------------------------------
FOR m  4
the optimal reward for gamma 0.9
{'A': 79.80001035898594, 'B': 93.45288211402925, 'C': 80.98345265619488}
the optimal policy
{'A': '2', 'B': '2', 'C': '2'}
the number of iterations required to converge 3
------------------------------------
FOR m  5
th

## 1.c Compare and contrast the behavior of Value Iteration and Gauss Seidel Value Iteraton


Gauss seidal performs better since it converges faster than value iteration as you can see below in almost all the different values of gamma.Also note that the optimal reward and optimal policy is same in both the cases i.e value iteraiton and gauss seidal value iteration and also matches with policy iteration values for respective gamma value.

In [98]:
gamma_values = [0.25,0.50,0.75,0.9]
for gamma in gamma_values:
    print("FOR VALUE ITERATION FOR LAMDA",gamma)
    print(results_vi[gamma]["Expected Reward"])
    print("the optimal policy")
    print(results_vi[gamma]["Policy"])
    print("the number of iterations required to converge",extra_info_vi[gamma]["iterations"])
    
    print("################################################")

    print("FOR GAUSS SEIDEL VALUE ITERATION",gamma)
    print(results_gs[gamma]["Expected Reward"])
    print("the optimal policy")
    print(results_gs[gamma]["Policy"])
    print("the number of iterations required to converge",extra_info_gs[gamma]["iterations"])
    print("------------------------------------")




FOR VALUE ITERATION FOR LAMDA 0.25
{'A': 11.274074070814656, 'B': 19.629629626369894, 'C': 10.207407404147988}
the optimal policy
{'A': '1', 'B': '2', 'C': '1'}
the number of iterations required to converge 16
################################################
FOR GAUSS SEIDEL VALUE ITERATION 0.25
{'A': 11.274074072135488, 'B': 19.62962962714145, 'C': 10.207407406785403}
the optimal policy
{'A': '1', 'B': '2', 'C': '1'}
the number of iterations required to converge 15
------------------------------------
FOR VALUE ITERATION FOR LAMDA 0.5
{'A': 18.298701293190973, 'B': 28.636363630853307, 'C': 17.15584415033383}
the optimal policy
{'A': '1', 'B': '2', 'C': '1'}
the number of iterations required to converge 32
################################################
FOR GAUSS SEIDEL VALUE ITERATION 0.5
{'A': 18.298701293837997, 'B': 28.63636363077955, 'C': 17.155844153026397}
the optimal policy
{'A': '1', 'B': '2', 'C': '1'}
the number of iterations required to converge 29
------------------------

# Submit to AIcrowd 🚀

In [ ]:
!DATASET_PATH=$AICROWD_DATASET_PATH aicrowd notebook submit -c iit-m-rl-assignment-2-taxi -a assets

No jupyter lab module found. Using jupyter notebook.
Using notebook: /content/Copy%20of%20IITM_Assignment_2_Taxi_Release.ipynb for submission...
Mounting Google Drive 💾
Your Google Drive will be mounted to access the colab notebook
Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.activity.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fexperimentsandconfigs%20https%3a%2f%2fwww.googleapis.com%2fauth%2fphotos.native&response_type=code

Enter your authorization code:
